In [28]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plot
from scipy import stats
from scipy import sparse
import scipy
from collections import defaultdict
import implicit
from implicit.als import AlternatingLeastSquares
import random
from sklearn.preprocessing import MinMaxScaler
from sklearn import metrics
from surprise import Reader, Dataset
from surprise.model_selection import train_test_split
from surprise import SVDpp

# import rectorch
# from rectorch.data import DataProcessing
# from rectorch.models.baseline import Random
# from rectorch.models.baseline import SLIM, Random, Popularity
# from rectorch.samplers import ArrayDummySampler, SparseDummySampler
# from rectorch.evaluation import evaluate
# from rectorch.utils import collect_results, prepare_for_prediction


# Data Parsing

In [29]:
# initialize data
%cd /Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/New_Research
item_threshold = 1 # used to filter out user/artist pairs that have been 
                   #listened to less than the threshold number of times
popular_artist_fraction = 0.2 # top cutoff for what we consider popular artists, in this case the top 20%
user_events_file = 'data/user_events.txt'
low_user_file = 'data/low_main_users.txt'
medium_user_file = 'data/medium_main_users.txt'
high_user_file = 'data/high_main_users.txt'

/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/New_Research


In [30]:
#read in user events file
cols = ['user', 'artist', 'album', 'track', 'timestamp']
df_events = pd.read_csv(user_events_file, sep='\t', names=cols)
print('No. of user events: ' + str(len(df_events)))
df_events.head() # check it is all read in properly

No. of user events: 28718087


user  artist  album  track   timestamp
0  31435741       2      4      4  1385212958
1  31435741       2      4      4  1385212642
2  31435741       2      4      4  1385212325
3  31435741       2      4      4  1385209508
4  31435741       2      4      4  1385209191

## User-Artist Matrix

In [31]:
# create unique user-artist matrix
df_events = df_events.groupby(['user', 'artist']).size().reset_index(name='listens')
print('No. user-artist pairs: ' + str(len(df_events)))
# each row contains a unique user-artist pair, along with how many times the
# user has listened to the artist
#df_events.sort_values(by=['user'])

No. user-artist pairs: 1755361


In [32]:
df_events.head(1400)

user   artist  listens
0     1021445       12       43
1     1021445       16        1
2     1021445       28        7
3     1021445       29        1
4     1021445       46        1
...       ...      ...      ...
1395  1021445  1864220        3
1396  1021445  1864221        4
1397  1021445  1864222        1
1398  1045479        3        9
1399  1045479       11        1

[1400 rows x 3 columns]

In [33]:
# filters out artist/user pairs who havent been listened two more than
# item_threshold amount of times to reduce potential load
# kept to 1 currently, so we dont filter out any data
df_events = df_events[df_events['listens'] >= item_threshold] 

# With 1, we see no difference between user-artist pairs here
print('No. filtered user-artist pairs: ' + str(len(df_events))) 

# here, we see the number of unique artists in our matrix
print('No. unique artists: ' + str(len(df_events['artist'].unique())))

No. filtered user-artist pairs: 1755361
No. unique artists: 352805


#### How many artists have users listened to?

In [34]:
# get matrix where each row is a user-id and how many artists they've 
#listened to
user_dist = df_events['user'].value_counts() 

# counts how many unique users there are. prints out user id & a count of how 
# many rows they're included in, which effectively shows how many artists 
# they listen to
num_users = len(user_dist)
print('Mean artists of all users: ' + str(user_dist.mean()))
print('Min artists of all users: ' + str(user_dist.min()))
print('Max artists of all users: ' + str(user_dist.max()))

user_dist.head()

Mean artists of all users: 585.1203333333333
Min artists of all users: 18
Max artists of all users: 4011


41888522    4011
4393555     3700
40029632    3678
26874346    3544
29736410    3529
Name: user, dtype: int64

#### How many users listen to an artist?

In [35]:
# get artist distribution
# same as previous but with artists, shows artist-id and how many times they
# were listened to buy unique users
artist_dist = df_events['artist'].value_counts()
num_artists = len(artist_dist)
print('No. artists: ' + str(num_artists))
df_events['artist'].value_counts().head

No. artists: 352805


<bound method NDFrame.head of 135        1389
1602       1359
46         1325
320        1297
27         1290
           ... 
3124286       1
1029181       1
1023032       1
1008679       1
3087545       1
Name: artist, Length: 352805, dtype: int64>

In [36]:
# get number of  popular artists
num_top_artists = int(popular_artist_fraction * num_artists)
artist_dist.head()
# getting the top top_fraction (0.2) percent of artists, so finding how many
# artists make up 20% of total artists, and then only using the artists those
#number of the most popular aritsts
top_artist_dist = artist_dist[:num_top_artists]
print('No. top artists: ' + str(len(top_artist_dist)))

No. top artists: 70561


In [37]:
# read in users
# user file is just user_id and their mainstreaminess value 
low_users = pd.read_csv(low_user_file, sep=',').set_index('user_id')
medium_users = pd.read_csv(medium_user_file, sep=',').set_index('user_id')
high_users = pd.read_csv(high_user_file, sep=',').set_index('user_id')
num_users = len(low_users) + len(medium_users) + len(high_users)
print('Num users: ' + str(num_users))

Num users: 3000


## Getting Users From Each Popularity Group & Their 10 Most Listened To Artists 

### (For Analysis of Streaming Service Algorithmic Bias)

In [28]:
toList = df_events.loc[df_events['user'] == 42845367].sort_values(by=['listens'], ascending=False)
toList.head() #grabbing random users top 10 artists in 1 of the 3 groups

user  artist  listens
1513514  42845367     495      205
1513639  42845367   15624      201
1513657  42845367   27107      171
1513483  42845367     163      156
1513485  42845367     172      156

In [29]:
to_list_2 = toList['artist'].tolist()[:20]
print(to_list_2)

[495, 15624, 27107, 163, 172, 4311, 8047, 7, 56, 245, 52741, 173416, 140, 1703, 3887, 42794, 1092, 2558, 54, 42835]


# Calculating GAP of User Profiles

In [41]:
# placeholder vars for numerator of GAPp, waiting to be divided by sie of group
low_gap_p = 0
medium_gap_p = 0
high_gap_p = 0
total_gap_p = 0
#Count for sanity check
low_count = 0
med_count = 0
high_count = 0

for u, df in df_events.groupby('user'):
    
    no_user_artists = len(set(df['artist'])) # profile size //number of artists in users profile
    # get popularity (= fraction of users interacted with item) of user items and calculate average of it
    user_pop_artist_fraq = sum(artist_dist[df['artist']] / num_users) / no_user_artists 
    
    if u in low_users.index: # get user group-specific values
        low_gap_p += user_pop_artist_fraq
        low_count += 1
    elif u in medium_users.index:
        medium_gap_p += user_pop_artist_fraq
        med_count += 1
    else:
        high_gap_p += user_pop_artist_fraq
        high_count += 1
        

total_gap_p = (low_gap_p + medium_gap_p + high_gap_p) / num_users
low_gap_p /= len(low_users) # average popularity of items/artists in low/med/high groups (gap = group average popularity)
medium_gap_p /= len(medium_users)
high_gap_p /= len(high_users)
print('Low count (for check): ' + str(low_count))
print('Med count (for check): ' + str(med_count))
print('High count (for check): ' + str(high_count))
print(low_gap_p)
print(medium_gap_p)
print(high_gap_p)

Low count (for check): 1000
Med count (for check): 1000
High count (for check): 1000
0.04963328792099549
0.054371119359489226
0.06286028679778642


### Min-Max Scaling Ratings (Not Using Right Now)

In [31]:
### Scale listening counts on a scale from 1-1000
"""scaled_df_events = pd.DataFrame()
for user_id, group in df_events.groupby('user'):
    #print(group)
    min_listens = group['listens'].min()
    max_listens = group['listens'].max()
    std = (group['listens'] - min_listens) / (max_listens - min_listens)
    scaled_listens = std * 999 + 1
    to_replace = group.copy()
    to_replace['listens'] = scaled_listens
    #print(to_replace)
    scaled_df_events = scaled_df_events.append(to_replace)
scaled_df_events.head()  """ 
#df_events.groupby('user').head()

"scaled_df_events = pd.DataFrame()\nfor user_id, group in df_events.groupby('user'):\n    #print(group)\n    min_listens = group['listens'].min()\n    max_listens = group['listens'].max()\n    std = (group['listens'] - min_listens) / (max_listens - min_listens)\n    scaled_listens = std * 999 + 1\n    to_replace = group.copy()\n    to_replace['listens'] = scaled_listens\n    #print(to_replace)\n    scaled_df_events = scaled_df_events.append(to_replace)\nscaled_df_events.head()  "

# Analysis of Alternating Least Squares with the Implicit Library

### Shaping the Data

In [32]:
#Normalize data to compare artist popularity vs recommendations
#Normalize artist popularity
normalized_artist_dist = pd.DataFrame(artist_dist)
normalized_artist_dist.columns = ['listens']
normalized_artist_dist['listens'] /= num_users
normalized_artist_dist.head()

num_times_recommended = pd.DataFrame(artist_dist)
num_times_recommended.columns = ['Recommendation Frequency']
num_times_recommended['Recommendation Frequency'] = 0
#num_times_recommended.head()
#normalized_artist_dist.head()
#For potential use with graphs, not being used right now

In [33]:
def user_events_file_to_lil_matrix():
    # Artist to User matrix where artist_user_matrix[a, u] = num of times user u listened to artist a

    # 352805, 3000 (total artists, users)
    rows, cols = 352805, 3000
    artist_user_matrix = scipy.sparse.lil_matrix((rows, cols), dtype=int)

    # user	artist	album	track	timestamp

    user_dict = {}  # simplify user id to 1, 2, 3 ...
    artist_dict = {}

    with open("/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/New_Research/data/user_events.txt", 'r') as fp:
        line = fp.readline()
        loop_count = 0
        while line:
            # get data from line
            line = fp.readline()
            parts = line.split("\t")

            # end case
            try:
                user_id = int(parts[0])
                artist_id = int(parts[1])
            except ValueError:
                print("end of file " + line)
                break

            # use user_dict to shorten user_id
            if user_id not in user_dict:
                # this user_id has not bee seen
                user_dict[user_id] = len(user_dict)
            user_idx = user_dict[user_id]

            # use track_dict to shorten track_id
            if artist_id not in artist_dict:
                # this user_id has not bee seen
                artist_dict[artist_id] = len(artist_dict)
            artist_idx = artist_dict[artist_id]

            # increment count of user to track
            artist_user_matrix[artist_idx, user_idx] += 1

            # progress marker
            loop_count = loop_count + 1
            if loop_count % 10000000 == 0:
                print(str(loop_count) + "/ 28718087")  # / num of lines in file

    print(len(user_dict))
    print(len(artist_dict))

    # helpful dicts for converting artist and user count back to their ids
    user_count_to_id_dict = {v: k for k, v in user_dict.items()}
    artist_count_to_id_dict = {v: k for k, v in artist_dict.items()}

    return artist_user_matrix, user_dict, artist_dict, user_count_to_id_dict, artist_count_to_id_dict


## FUNCTIONS FROM from jmsteinw's blog post ## a_u_tuple


In [34]:
def make_train(ratings, pct_test=0.2):
    '''
    This function will take in the original user-item matrix and "mask" a percentage of the original ratings where a
    user-item interaction has taken place for use as a test set. The test set will contain all of the original ratings,
    while the training set replaces the specified percentage of them with a zero in the original ratings matrix.

    parameters:

    ratings - the original ratings matrix from which you want to generate a train/test set. Test is just a complete
    copy of the original set. This is in the form of a sparse csr_matrix.

    pct_test - The percentage of user-item interactions where an interaction took place that you want to mask in the
    training set for later comparison to the test set, which contains all of the original ratings.

    returns:

    training_set - The altered version of the original data with a certain percentage of the user-item pairs
    that originally had interaction set back to zero.

    test_set - A copy of the original ratings matrix, unaltered, so it can be used to see how the rank order
    compares with the actual interactions.

    user_inds - From the randomly selected user-item indices, which user rows were altered in the training data.
    This will be necessary later when evaluating the performance via AUC.
    '''
    test_set = ratings.copy()  # Make a copy of the original set to be the test set.
    test_set[test_set != 0] = 1  # Store the test set as a binary preference matrix
    training_set = ratings.copy()  # Make a copy of the original data we can alter as our training set.
    nonzero_inds = training_set.nonzero()  # Find the indices in the ratings data where an interaction exists
    nonzero_pairs = list(zip(nonzero_inds[0], nonzero_inds[1]))  # Zip these pairs together of user,item index into list
    random.seed(0)  # Set the random seed to zero for reproducibility
    num_samples = int(
        np.ceil(pct_test * len(nonzero_pairs)))  # Round the number of samples needed to the nearest integer
    samples = random.sample(nonzero_pairs, num_samples)  # Sample a random number of user-item pairs without replacement
    user_inds = [index[0] for index in samples]  # Get the user row indices
    item_inds = [index[1] for index in samples]  # Get the item column indices
    training_set[user_inds, item_inds] = 0  # Assign all of the randomly chosen user-item pairs to zero
    training_set.eliminate_zeros()  # Get rid of zeros in sparse array storage after update to save space
    return training_set, test_set, list(set(user_inds))  # Output the unique list of user rows that were altered


# Usage
# a_to_u_train, a_to_u_test, altered_users = make_train(csr_sparse_matrix, pct_test = 0.2)

In [35]:
print("start calculating matrix")
a_u_tuple = user_events_file_to_lil_matrix()
a_u_matrix = a_u_tuple[0] #artist/user matrix
back_to_user_id = a_u_tuple[3] #dictionary to convert smaller user ids to original
back_to_artist_id = a_u_tuple[4]# same above but for artists
print("done")

start calculating matrix
10000000/ 28718087
20000000/ 28718087
end of file 
3000
352805
done


In [36]:
u_to_a_train, u_to_a_test, altered_users = make_train(a_u_matrix.T.tocsr(), pct_test=0.2) #makes training/test set
print("done")

done


### Training the Algorithm

In [37]:
# split original matrix into user vector and artist vector through ALS
user_vecs, artists_vecs = implicit.alternating_least_squares((u_to_a_train).astype('double'),iterations=50, factors=50)
print("done")

[10:23:43-270421]  This method is deprecated. Please use the AlternatingLeastSquares class instead
[10:23:43-270421]  Intel MKL BLAS detected. Its highly recommend to set the environment variable 'export MKL_NUM_THREADS=1' to disable its internal multithreading



done


In [38]:
print(np.array(user_vecs[0,:].dot(artists_vecs.T))[:10]) # gets first 5 recommendations

[0.73036563 0.8968482  0.32901415 0.7735475  0.9963831  0.85969764
 0.88231444 0.6687855  0.7613538  0.2026935 ]


### Get Top N Recommendations

In [16]:
def get_top_artists_implicit(user_vecs, artists_vecs, mf_train, back_to_user_id,back_to_artist_id, num=10):
    """Return the top-N recommendation for each user from a set of predictions.

    Args:
        user_vecs: the feature vector for users
        mf_train: training matrix
        artists_vecs: the feature vector for artists
        back_to_user_id: dictionary to convert back to original user id
        back_to_artist_id: dictionary to convert back to original artist id
        n(int): The number of recommendation to output for each user. Default
            is 10.

    Returns:
    A dict where keys are user (raw) ids and values are lists of tuples:
        [(raw item id), ...] of size n.
    """
    top_artists_dict = defaultdict(list)
        # creating dictionary where user id is the key, and the val is a list of tuples of the artist id and 
        # the rating it thinks the user would give it
        
    for user_id in range(len(user_vecs)):
        
        pref_vec = mf_train[user_id,:].toarray() # Get the ratings from the training set ratings matrix
        pref_vec = pref_vec.reshape(-1)
        pref_vec =  pref_vec + 1 # Add 1 to everything, so that artists not listened to yet are equal to 1
        pref_vec[pref_vec > 1] = 0 # Make everything already purchased zero
        
        rec_vector = user_vecs[user_id,:].dot(artists_vecs.T) # Get dot product of user vector and all artist vectors
        # Scale this recommendation vector between 0 and 1
        
        min_max = MinMaxScaler()
        rec_vector_scaled = min_max.fit_transform(rec_vector.reshape(-1,1))[:,0] 
        recommend_vector = pref_vec*rec_vector_scaled 
        # Items already purchased have their recommendation multiplied by zero
        
        product_idx = np.argsort(recommend_vector)[::-1][:num] # Sort the indices of the items into order 
        # of best recommendations
        rec_list = [] # start empty list to store items
        actual_user_id = back_to_user_id[user_id]
        #print(actual_user_id)
        
        for index in product_idx:
            actual_artist_id = back_to_artist_id[index]
            rec_list.append(actual_artist_id)
            
        top_artists_dict[actual_user_id] = rec_list
    print("done")
    return top_artists_dict
    
    

In [40]:
implicit_top_n = get_top_artists_implicit(user_vecs, artists_vecs, u_to_a_train,back_to_user_id, back_to_artist_id,num = 10) 
#gets top n artists for all the users in the dataset
print("done")

done
done


In [41]:
print(implicit_top_n[6532902]) #testing out getting top recommendations for a user

[6443, 15483, 2908, 2836, 1998, 11058, 16711, 43, 6236, 2442]


In [42]:
print(artist_dist[6443]) #getting popularity of artist by indexing by id

180


### Calculating GAPr and Delta GAP for ALS

In [43]:
# Train and test the four algorithms on our data set
low_gap_r_list = []
medium_gap_r_list = []
high_gap_r_list = []
total_gap_r_list= []
#keeps track of the GAPr of each of the algs

alg_recommendations = [] #Keeps track of how many times each artist was recommended

#Will put for loop here with training, but for now we already have predictions
    
num_times_recommended = pd.DataFrame(artist_dist)
num_times_recommended.columns = ['Recommendation Frequency']
num_times_recommended['Recommendation Frequency'] = 0 #resets for each algorithm
    
    
# resets to 0 before calculating for new alg
low_gap_r = 0
medium_gap_r = 0
high_gap_r = 0
    
#keeps track of group size since it is unpredictable since the test set is selected randomly
num_low_users = 0
num_medium_users = 0
num_high_users = 0
    
#keeps track of the mean absolute error of the current alg
low_mae = 0
medium_mae = 0
high_mae = 0
top_artists = implicit_top_n #Gets the top N recommendations for each user
    

for user_id, ratings in top_artists.items():
    artist_id_list = [] #user profile size to compute top fraction in GAPr
    for artist_id in ratings:
            
        artist_id_list.append(artist_id)
        num_times_recommended.loc[artist_id] += 1 #increments the number of times the artist was recommended

    gap = sum(artist_dist[artist_id_list]/ num_users) / len(artist_id_list) #fraction in numerator for GAPr
    #print("gap:" ,gap)
    if user_id in low_users.index: #summation of all of the top fractions to compute numerator for GAPr
        low_gap_r += gap
        num_low_users += 1 #increments group size to get the denominator to compute GAPr

    elif user_id in medium_users.index:
        medium_gap_r += gap
        num_medium_users += 1

    elif user_id in high_users.index:
        high_gap_r += gap
        num_high_users += 1
alg_recommendations.append(num_times_recommended)
            
total_gap_r = (low_gap_r + medium_gap_r + high_gap_r) / (num_low_users + num_medium_users + num_high_users)
low_gap_r = low_gap_r / num_low_users #Computing GAPr for each group size for each algorithm
medium_gap_r = medium_gap_r / num_medium_users
high_gap_r = high_gap_r / num_high_users

total_gap_r_list.append(total_gap_r)
low_gap_r_list.append(low_gap_r)
medium_gap_r_list.append(medium_gap_r)
high_gap_r_list.append(high_gap_r)

print("done")

done


In [43]:
#Computes change in GAP for each RecSys alg
delta_gap_low_list = []
delta_gap_medium_list = []
delta_gap_high_list = []
delta_gap_total_list = []

for i in range(len(low_gap_r_list)):
    delta_gap_low = ((low_gap_r_list[i] - low_gap_p) / low_gap_p)
    delta_gap_medium = ((medium_gap_r_list[i] - medium_gap_p) / medium_gap_p)
    delta_gap_high = ((high_gap_r_list[i] - high_gap_p) / high_gap_p)
    delta_gap_total = ((total_gap_r_list[i] - total_gap_p) / total_gap_p)
    
    delta_gap_low_list.append(delta_gap_low)
    delta_gap_medium_list.append(delta_gap_medium)
    delta_gap_high_list.append(delta_gap_high)
    delta_gap_total_list.append(delta_gap_total)
    
print(delta_gap_low_list[0])

print(delta_gap_medium_list[0])

print(delta_gap_high_list[0])

print(delta_gap_total_list[0])


2.4569889301057035
2.17545012520779
1.796262451276512
2.1163397100917085


### Calculating AUC for ALS

In [45]:
def auc_score(predictions, test):
    '''
    This simple function will output the area under the curve using sklearn's metrics.

    parameters:

    - predictions: your prediction output

    - test: the actual target result you are comparing to

    returns:

    - AUC (area under the Receiver Operating Characterisic curve)
    '''
    # shuffle list of predictions (shuffle function)
    # shuffling dissassociates link to artist - > roc of .5 (random)
    fpr, tpr, thresholds = metrics.roc_curve(test, predictions)
    return metrics.auc(fpr, tpr)

In [46]:
def calc_mean_auc(training_set, altered_users, predictions, test_set):
    '''
    This function will calculate the mean AUC by user for any user that had their user-item matrix altered.

    parameters:

    training_set - The training set resulting from make_train, where a certain percentage of the original
    user/item interactions are reset to zero to hide them from the model

    predictions - The matrix of your predicted ratings for each user/item pair as output from the implicit MF.
    These should be stored in a list, with user vectors as item zero and item vectors as item one.

    altered_users - The indices of the users where at least one user/item pair was altered from make_train function

    test_set - The test set constucted earlier from make_train function

    returns:

    The mean AUC (area under the Receiver Operator Characteristic curve) of the test set only on user-item interactions
    there were originally zero to test ranking ability in addition to the most popular items as a benchmark.
    '''

    store_auc = []  # An empty list to store the AUC for each user that had an item removed from the training set
    popularity_auc = []  # To store popular AUC scores
    pop_items = np.array(test_set.sum(axis=0)).reshape(-1)  # Get sum of item iteractions to find most popular
    item_vecs = predictions[1]
    for user in altered_users:  # Iterate through each user that had an item altered
        training_row = training_set[user, :].toarray().reshape(-1)  # Get the training set row
        zero_inds = np.where(training_row == 0)  # Find where the interaction had not yet occurred
        # Get the predicted values based on our user/item vectors
        user_vec = predictions[0][user, :]
        pred = user_vec.dot(item_vecs).toarray()[0, zero_inds].reshape(-1)
        # Get only the items that were originally zero
        # Select all ratings from the MF prediction for this user that originally had no iteraction
        actual = test_set[user, :].toarray()[0, zero_inds].reshape(-1)
        # Select the binarized yes/no interaction pairs from the original full data
        # that align with the same pairs in training
        pop = pop_items[zero_inds]  # Get the item popularity for our chosen items
        curr_auc_score = auc_score(pred, actual)
        store_auc.append(curr_auc_score)  # Calculate AUC for the given user and store
        curr_pop_score = auc_score(pop, actual)
        popularity_auc.append(curr_pop_score)  # Calculate AUC using most popular and score
        # print(user, "\t", curr_auc_score , "\t", curr_pop_score)
    # End users iteration

    return float('%.3f' % np.mean(store_auc)), float('%.3f' % np.mean(popularity_auc))
    # Return the mean AUC rounded to three decimal places for both test and popularity benchmark


In [47]:
rec_auc, pop_auc = calc_mean_auc(u_to_a_train, altered_users,[sparse.csr_matrix(user_vecs), sparse.csr_matrix(artists_vecs.T)],
                                             u_to_a_test)
print(rec_auc)
print(pop_auc)

0.873
0.883


# Rectorch Training

### Setting Up The Data

In [48]:
data_events = df_events.copy(deep=True)
data_events.to_csv('data_events.csv',index=False,header=False )
print("done")

done


In [49]:
%cd /Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main 
!git clone -b dev https://github.com/makgyver/rectorch.git
%cd rectorch
!pip install -r requirements.txt

/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main
fatal: destination path 'rectorch' already exists and is not an empty directory.
/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/rectorch


In [65]:
%cd /Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/New_Research
cfg_data_test = {
    "processing": {
        "data_path": "data_events.csv",
        "threshold": 0,
        "separator": ",",
        "header": None,
        "u_min": 50,
        "i_min": 50
    },
    "splitting": {
        "split_type": "horizontal",
        "sort_by": None,
        "seed": 98765,
        "shuffle": True,
        "valid_size": 0.1,
        "test_size": 0.1,
        "test_prop": 0.2
    }
}

cfg_data_full = {
    "processing": {
        "data_path": "data_events.csv",
        "threshold": 0,
        "separator": ",",
        "header": None,
        "u_min": 0,
        "i_min": 0
    },
    "splitting": {
        "split_type": "horizontal",
        "sort_by": None,
        "seed": 98765,
        "shuffle": True,
        "valid_size": 0.1,
        "test_size": 0.1,
        "test_prop": 0.2
    }
}

/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/New_Research


In [66]:
from rectorch.data import DataProcessing
dataset = DataProcessing(cfg_data_test).process_and_split()
dataset

[14:05:50-300421]  Reading raw data file data_events.csv.
[14:05:56-300421]  Applying filtering.
[14:05:57-300421]  Filtered 988317 ratings.
[14:05:57-300421]  Shuffling data.
[14:05:57-300421]  Creating training, validation and test set.


Dataset(n_users=2804, n_items=5131, n_ratings=767044)

In [67]:
from rectorch.models.baseline import SLIM, Random, Popularity
from rectorch.data import DataProcessing
from rectorch.samplers import ArrayDummySampler, SparseDummySampler
from rectorch.evaluation import evaluate
from rectorch.utils import collect_results, prepare_for_prediction

sparse_sampler = SparseDummySampler(dataset, mode="train")

### Grid Search on SLIM

In [38]:
lambda_vals =  np.array([0.0001, 0.0003, 0.001, 0.003, 0.01, 0.03, 0.1, 0.3])
beta_vals =  np.array([0.0001, 0.0003, 0.001, 0.003, 0.01, 0.03, 0.1, 0.3])


error = np.zeros([lambda_vals.size,beta_vals.size])

sparse_sampler = SparseDummySampler(dataset, mode="train")
for i in range(len(lambda_vals)):
    for j in range(len(beta_vals)):
        sparse_sampler.train()
        
        slim = SLIM(l1_reg=lambda_vals[i], l2_reg=beta_vals[j])
        slim.train(sparse_sampler)
        
        sparse_sampler.test()
        
        results = evaluate(slim, sparse_sampler, ["ap@5000"])
        error[i,j] = collect_results(results).get("ap@5000")[0]
        print(collect_results(results))
        print(collect_results(results).get("ap@5000")[0])
        
print(error)
        
minError = np.argwhere(error == np.amax(error))
Lambda = lambda_vals[(minError[0][0])]
beta = beta_vals[(minError[0][1])]
print(Lambda)
print(beta)


/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/rectorch/rectorch/metrics.py:245: RuntimeWarning: invalid value encountered in multiply
  num = pred_scores * ground_truth


{'ap@5000': (0.12851225090805365, 0.0801624333389584)}
0.12851225090805365


/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/rectorch/rectorch/metrics.py:245: RuntimeWarning: invalid value encountered in multiply
  num = pred_scores * ground_truth


{'ap@5000': (0.12882273749332865, 0.0800273683108513)}
0.12882273749332865


/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/rectorch/rectorch/metrics.py:245: RuntimeWarning: invalid value encountered in multiply
  num = pred_scores * ground_truth


...

{'ap@5000': (0.0, 0.0)}
0.0


/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/rectorch/rectorch/metrics.py:245: RuntimeWarning: invalid value encountered in multiply
  num = pred_scores * ground_truth


{'ap@5000': (0.0, 0.0)}
0.0


/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/rectorch/rectorch/metrics.py:245: RuntimeWarning: invalid value encountered in multiply
  num = pred_scores * ground_truth


{'ap@5000': (0.0, 0.0)}
0.0
[[0.12851225 0.12882274 0.12988474 0.13238474 0.13731052 0.1409856
  0.13895127 0.13062076]
 [0.13091648 0.13111136 0.13198311 0.13424593 0.13834158 0.14131486
  0.13877306 0.1303479 ]
 [0.13537905 0.1356008  0.13626014 0.13759539 0.13994234 0.14052816
  0.13709833 0.12844514]
 [0.13178956 0.13176923 0.1318709  0.13185112 0.13179571 0.13079366
  0.12743128 0.11991232]
 [0.10004898 0.10006405 0.10001021 0.09991465 0.09985705 0.09944694
  0.09835089 0.09482609]
 [0.06335927 0.06332919 0.06334652 0.06346481 0.06355087 0.06365465
  0.06411409 0.06393328]
 [0.02397401 0.02395416 0.02382432 0.02411175 0.02396452 0.02405855
  0.02473613 0.02574048]
 [0.         0.         0.         0.         0.         0.
  0.         0.        ]]
0.0003
0.03


### Training SLIM on Partial Dataset with Tuned Parameters

In [68]:
#Learned best Lambda = 0.0003 and best Beta = 0.03
Lambda=0.0003
beta=0.03
sparse_sampler.train()
slim = SLIM(l1_reg=Lambda, l2_reg=beta)
slim.train(sparse_sampler)

[14:06:10-300421]  | item 513/5131 | ms/user 22.50 |
[14:06:23-300421]  | item 1026/5131 | ms/user 25.27 |
[14:06:36-300421]  | item 1539/5131 | ms/user 25.02 |
[14:06:49-300421]  | item 2052/5131 | ms/user 24.50 |
[14:07:01-300421]  | item 2565/5131 | ms/user 24.02 |
[14:07:13-300421]  | item 3078/5131 | ms/user 23.14 |
[14:07:24-300421]  | item 3591/5131 | ms/user 22.63 |
[14:07:37-300421]  | item 4104/5131 | ms/user 24.76 |
[14:07:49-300421]  | item 4617/5131 | ms/user 23.68 |
[14:08:03-300421]  | item 5130/5131 | ms/user 26.57 |
[14:08:03-300421]  | training complete | total training time 124.26 s |


In [70]:
sparse_sampler.test()
results = evaluate(slim, sparse_sampler, ["ap@5000","auc"])
collect_results(results)

{'ap@5000': (0.14131007498186307, 0.08234862658665092),
 'auc': (0.91083026, 0.047491606)}

In [71]:
slim.save_model("slimHorizontal")

[14:09:46-300421]  Saving SLIM model to slimHorizontal...
[14:09:46-300421]  Model saved!


In [72]:
slim2 = SLIM(l1_reg=.0003, l2_reg=.03)
slim2 = slim2.load_model("slimHorizontal")

[14:09:47-300421]  Loading SLIM model from slimHorizontal...
[14:09:47-300421]  Model loaded!


In [73]:
results = evaluate(slim2, sparse_sampler, ["ap@5000"])
collect_results(results)

{'ap@5000': (0.14131007498186307, 0.08234862658665092)}

### Getting Predictions Matrix

In [74]:
sparse_sampler.test()
for _, (data_input, ground_truth) in enumerate(sparse_sampler):
    data_input, ground_truth = prepare_for_prediction(data_input, ground_truth)
    predictions = slim2.predict(*data_input)[0].cpu().numpy()
print(predictions)
print(ground_truth)

print(len(predictions))
print(predictions[0,:])

[[      -inf       -inf       -inf ... 0.04991516 0.45460108 0.00772082]
 [0.00049505 0.0020329        -inf ... 0.         0.         0.00243843]
 [0.07106647       -inf 0.26445588 ... 0.00566066 0.02116269 0.01083257]
 ...
 [0.03637528 0.05174621 0.07925012 ... 0.         0.               -inf]
 [0.10318983 0.07759615 0.25242814 ... 0.00383702 0.15934207       -inf]
 [0.03482188 0.00276908 0.03123361 ... 0.         0.03244679 0.        ]]
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
2804
[      -inf       -inf       -inf ... 0.04991516 0.45460108 0.00772082]


### Getting Top N Artists for SLIM (Works with Any Rectorch Algorithm)

In [75]:
def get_top_artists(predictions, back_to_user_id,back_to_artist_id, num=10):
    """Return the top-N recommendation for each user from a set of predictions.

    Args:
        Predictions: the Prediction vectors
        back_to_user_id: dictionary to convert back to original user id
        back_to_artist_id: dictionary to convert back to original artist id
        num(int): The number of recommendation to output for each user. Default
            is 10.

    Returns:
    A dict where keys are user (raw) ids and values are lists of tuples:
        [(raw item id), ...] of size n.
    """
    top_artists_dict = defaultdict(list)
        # creating dictionary where user id is the key, and the val is a list of tuples of the artist id and 
        # the rating it thinks the user would give it
        
    for user_id in range(len(predictions)):
        
        rec_vector = predictions[user_id,:].copy()
        #print(rec_vector)
        
        recommend_vector = rec_vector
        
        product_idx = np.argsort(recommend_vector)[::-1][:num] # Sort the indices of the items into order 
        # of best recommendations
        rec_list = [] # start empty list to store items
        actual_user_id = back_to_user_id[user_id]
        #print(actual_user_id)
        
        for index in product_idx:
            actual_artist_id = back_to_artist_id[index]
            rec_list.append(actual_artist_id)
            
        top_artists_dict[actual_user_id] = rec_list
    print("done")
    return top_artists_dict
    
    

#### Reversing the matrices given by the dataset so we can get the original artist and user ids

In [81]:
id2u =  dict(map(reversed, dataset.u2id.items())) #dict for putting user ids back to normal
id2i = dict(map(reversed, dataset.i2id.items())) #dict for translating artist ids back to normal

In [98]:
rectorch_top_n = get_top_artists(predictions, id2u, id2i,10)

done


In [99]:
rectorch_top_n[6532902]

[2836, 17292, 6443, 17302, 35098, 7941, 7463, 1804, 15629, 18830]

### Calculating GAPr and Delta GAP for Rectorch Algorithms (SLIM)

In [100]:
# Train and test the four algorithms on our data set
low_gap_r_list = []
medium_gap_r_list = []
high_gap_r_list = []
total_gap_r_list= []
#keeps track of the GAPr of each of the algs

alg_recommendations = [] #Keeps track of how many times each artist was recommended

#Will put for loop here with training, but for now we already have predictions
    
num_times_recommended = pd.DataFrame(artist_dist)
num_times_recommended.columns = ['Recommendation Frequency']
num_times_recommended['Recommendation Frequency'] = 0 #resets for each algorithm
    
    
# resets to 0 before calculating for new alg
low_gap_r = 0
medium_gap_r = 0
high_gap_r = 0
    
#keeps track of group size since it is unpredictable since the test set is selected randomly
num_low_users = 0
num_medium_users = 0
num_high_users = 0
    
#keeps track of the mean absolute error of the current alg
low_mae = 0
medium_mae = 0
high_mae = 0
top_artists = rectorch_top_n #Gets the top N recommendations for each user
    

for user_id, ratings in top_artists.items():
    artist_id_list = [] #user profile size to compute top fraction in GAPr
    for artist_id in ratings:
            
        artist_id_list.append(artist_id)
        num_times_recommended.loc[artist_id] += 1 #increments the number of times the artist was recommended

    gap = sum(artist_dist[artist_id_list]/ num_users) / len(artist_id_list) #fraction in numerator for GAPr
    #print("gap:" ,gap)
    if user_id in low_users.index: #summation of all of the top fractions to compute numerator for GAPr
        low_gap_r += gap
        num_low_users += 1 #increments group size to get the denominator to compute GAPr

    elif user_id in medium_users.index:
        medium_gap_r += gap
        num_medium_users += 1

    elif user_id in high_users.index:
        high_gap_r += gap
        num_high_users += 1
alg_recommendations.append(num_times_recommended)
            
total_gap_r = (low_gap_r + medium_gap_r + high_gap_r) / (num_low_users + num_medium_users + num_high_users)
low_gap_r = low_gap_r / num_low_users #Computing GAPr for each group size for each algorithm
medium_gap_r = medium_gap_r / num_medium_users
high_gap_r = high_gap_r / num_high_users

total_gap_r_list.append(total_gap_r)
low_gap_r_list.append(low_gap_r)
medium_gap_r_list.append(medium_gap_r)
high_gap_r_list.append(high_gap_r)

print("done")

done


In [101]:
#Computes change in GAP for each RecSys alg
delta_gap_low_list = []
delta_gap_medium_list = []
delta_gap_high_list = []
delta_gap_total_list = []

for i in range(len(low_gap_r_list)):
    delta_gap_low = ((low_gap_r_list[i] - low_gap_p) / low_gap_p)
    delta_gap_medium = ((medium_gap_r_list[i] - medium_gap_p) / medium_gap_p)
    delta_gap_high = ((high_gap_r_list[i] - high_gap_p) / high_gap_p)
    delta_gap_total = ((total_gap_r_list[i] - total_gap_p) / total_gap_p)
    
    delta_gap_low_list.append(delta_gap_low)
    delta_gap_medium_list.append(delta_gap_medium)
    delta_gap_high_list.append(delta_gap_high)
    delta_gap_total_list.append(delta_gap_total)
    
print(delta_gap_low_list[0])

print(delta_gap_medium_list[0])

print(delta_gap_high_list[0])

print(delta_gap_total_list[0])

2.6633147542831384
2.7211069034969353
2.4091488209561827
2.5878339248338365


### Multi VAE

In [2]:
#data.csv-->multi vae
#dr_frame-->multi vae
%cd /Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/rectorch
import rectorch
from rectorch.data import DataProcessing
from rectorch.samplers import DataSampler
from rectorch.models.nn.multvae import MultVAE
from rectorch.evaluation import evaluate
from rectorch.utils import collect_results, prepare_for_prediction

/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/rectorch


In [3]:
%cd /Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/New_Research
cfg_data_test = {
    "processing": {
        "data_path": "data_events.csv",
        "threshold": 0,
        "separator": ",",
        "header": None,
        "u_min": 50,
        "i_min": 50
    },
    "splitting": {
        "split_type": "horizontal",
        "sort_by": None,
        "seed": 98765,
        "shuffle": True,
        "valid_size": 0.1,
        "test_size": 0.1,
        "test_prop": 0.2
    }
}


cfg_data_full = {
    "processing": {
        "data_path": "data_events.csv",
        "threshold": 0,
        "separator": ",",
        "header": None,
        "u_min": 0,
        "i_min": 0
    },
    "splitting": {
        "split_type": "horizontal",
        "sort_by": None,
        "seed": 98765,
        "shuffle": True,
        "valid_size": 0.1,
        "test_size": 0.1,
        "test_prop": 0.2
    }
}

/Users/sunnyzhang/Desktop/Cornell Spring 21/CS 4999 Research/codes/LFM-1b-surprise-and-implicit-analysis-main/New_Research


In [4]:
## the code from multivae tutorial

dataset = DataProcessing(cfg_data_test).process_and_split()
dataset
sampler = DataSampler(dataset, mode="train", batch_size=500)

dataset_full = DataProcessing(cfg_data_full).process_and_split()
dataset_full
sampler_full = DataSampler(dataset_full, mode="train", batch_size=500)



[13:38:36-300421]  Reading raw data file data_events.csv.
[13:38:43-300421]  Applying filtering.
[13:38:43-300421]  NumExpr defaulting to 8 threads.
[13:38:43-300421]  Filtered 988317 ratings.
[13:38:43-300421]  Shuffling data.
[13:38:43-300421]  Creating training, validation and test set.
[13:38:45-300421]  Reading raw data file data_events.csv.
[13:38:51-300421]  Applying filtering.
[13:38:51-300421]  Shuffling data.
[13:38:51-300421]  Creating training, validation and test set.
[13:38:52-300421]  Skipped 25021 ratings in validation set.
[13:38:52-300421]  Skipped 24878 ratings in test set.


In [5]:
# train parameters: beta, anneal steps [interate through several to find the least error one]
# choose the best one and use that param to train
# save the model
# get the prediction matrix
# then get the top n artist for MultiVAE
# Calculate GAPr and Delta GAP
# then we are done!

### Grid Search on MultiVAE

In [5]:
# add drop out rate to tune the params
print("start running the code")
import numpy as np

# # the following is a small test cases
# anneal_vals=np.array([10000])
# beta_vals =  np.array([0.0001])
# drop_vals=[0.1]

anneal_vals =  np.array([0, 1000, 10000, 100000, 300000, 500000,1000000,3000000,5000000])
beta_vals =  np.array([0.0001, 0.0003, 0.001, 0.003, 0.01, 0.03, 0.1, 0.3])
drop_vals = np.array([0,0.1, 0.3, 0.5, 0.6, 0.8])

error = np.zeros([anneal_vals.size, beta_vals.size, drop_vals.size])

sampler = DataSampler(dataset, mode="train",batch_size=500)
for i in range(len(anneal_vals)):
    for j in range(len(beta_vals)):
        for w in range(len(drop_vals)):
            sampler.train()
        
            multivae = MultVAE(
                  dec_dims=[200,600,dataset.n_items],
                  enc_dims=None,
                  dropout=drop_vals[w],
                  beta=beta_vals[j],
                  anneal_steps=anneal_vals[i],
                  opt_conf=None,
                  device="cpu",
                  trainer=None)
        
            multivae.train(sampler)
        
            sampler.test()
          # ap@5000 is the mean average precision
    
            results = evaluate(multivae, sampler, ["ap@5000"])
            error[i,j,w] = collect_results(results).get("ap@5000")[0]
            print(collect_results(results))
            print(collect_results(results).get("ap@5000")[0])
            
print("final printing starts")
print(error)
# now error records the average precision, so higher the precision, the better; amax used here
minError = np.argwhere(error == np.amax(error))

print(minError)
Anneal = anneal_vals[(minError[0][0])]
beta = beta_vals[(minError[0][1])]
dropout = drop_vals[(minError[0][2])]
print(Anneal)
print(beta)
print(dropout)


start running the code


[10:30:14-240421]  | epoch 1 | loss 1883.5320 | total time: 1.46s |
[10:30:16-240421]  | epoch 2 | loss 1811.8056 | total time: 1.39s |
[10:30:17-240421]  | epoch 3 | loss 1810.1237 | total time: 1.37s |
[10:30:19-240421]  | epoch 4 | loss 1810.3440 | total time: 1.36s |
[10:30:20-240421]  | epoch 5 | loss 1799.7027 | total time: 1.42s |
[10:30:21-240421]  | epoch 6 | loss 1796.7022 | total time: 1.40s |
[10:30:23-240421]  | epoch 7 | loss 1783.3707 | total time: 1.40s |
[10:30:24-240421]  | epoch 8 | loss 1765.7042 | total time: 1.39s |
[10:30:26-240421]  | epoch 9 | loss 1731.5073 | total time: 1.48s |
[10:30:27-240421]  | epoch 10 | loss 1718.1167 | total time: 1.39s |
[10:30:28-240421]  | epoch 11 | loss 1705.1287 | total time: 1.35s |
[10:30:30-240421]  | epoch 12 | loss 1707.5653 | total time: 1.35s |
[10:30:31-240421]  | epoch 13 | loss 1698.0037 | total time: 1.38s |
[10:30:33-240421]  | epoch 14 | loss 1688.5321 | total time: 1.41s |
[10:30:34-240421]  | epoch 15 | loss 1683.9

[10:33:07-240421]  | epoch 120 | loss 1432.6436 | total time: 1.47s |
[10:33:08-240421]  | epoch 121 | loss 1438.4800 | total time: 1.44s |
[10:33:09-240421]  | epoch 122 | loss 1440.7233 | total time: 1.44s |
[10:33:11-240421]  | epoch 123 | loss 1430.3516 | total time: 1.46s |
[10:33:12-240421]  | epoch 124 | loss 1432.1070 | total time: 1.42s |
[10:33:14-240421]  | epoch 125 | loss 1427.4035 | total time: 1.44s |
[10:33:15-240421]  | epoch 126 | loss 1422.9920 | total time: 1.45s |
[10:33:17-240421]  | epoch 127 | loss 1432.2929 | total time: 1.50s |
[10:33:18-240421]  | epoch 128 | loss 1433.1235 | total time: 1.47s |
[10:33:20-240421]  | epoch 129 | loss 1425.3569 | total time: 1.48s |
[10:33:21-240421]  | epoch 130 | loss 1426.4532 | total time: 1.45s |
[10:33:23-240421]  | epoch 131 | loss 1425.8279 | total time: 1.49s |
[10:33:24-240421]  | epoch 132 | loss 1426.4793 | total time: 1.47s |
[10:33:25-240421]  | epoch 133 | loss 1418.7121 | total time: 1.44s |
[10:33:27-240421]  |

{'ap@5000': (0.0767513911526407, 0.051736437940940086)}
0.0767513911526407


[10:35:06-240421]  | epoch 1 | loss 1893.6998 | total time: 1.49s |
[10:35:07-240421]  | epoch 2 | loss 1821.8986 | total time: 1.49s |
[10:35:09-240421]  | epoch 3 | loss 1820.6821 | total time: 1.49s |
[10:35:10-240421]  | epoch 4 | loss 1810.6940 | total time: 1.53s |
[10:35:12-240421]  | epoch 5 | loss 1796.7883 | total time: 1.50s |
[10:35:13-240421]  | epoch 6 | loss 1795.9263 | total time: 1.48s |
[10:35:15-240421]  | epoch 7 | loss 1786.1595 | total time: 1.52s |
[10:35:16-240421]  | epoch 8 | loss 1767.6208 | total time: 1.52s |
[10:35:18-240421]  | epoch 9 | loss 1757.8359 | total time: 1.49s |
[10:35:19-240421]  | epoch 10 | loss 1727.6151 | total time: 1.50s |
[10:35:21-240421]  | epoch 11 | loss 1712.1139 | total time: 1.53s |
[10:35:22-240421]  | epoch 12 | loss 1704.1098 | total time: 1.53s |
[10:35:24-240421]  | epoch 13 | loss 1688.7701 | total time: 1.53s |
[10:35:25-240421]  | epoch 14 | loss 1688.5701 | total time: 1.54s |
[10:35:27-240421]  | epoch 15 | loss 1678.9

...

[13:06:07-260421]  | epoch 120 | loss 1516.4078 | total time: 1.46s |
[13:06:09-260421]  | epoch 121 | loss 1529.4899 | total time: 1.46s |
[13:06:10-260421]  | epoch 122 | loss 1520.7601 | total time: 1.46s |
[13:06:12-260421]  | epoch 123 | loss 1519.0735 | total time: 1.47s |
[13:06:13-260421]  | epoch 124 | loss 1518.6055 | total time: 1.45s |
[13:06:15-260421]  | epoch 125 | loss 1521.3170 | total time: 1.45s |
[13:06:16-260421]  | epoch 126 | loss 1514.1537 | total time: 1.46s |
[13:06:17-260421]  | epoch 127 | loss 1510.2165 | total time: 1.45s |
[13:06:19-260421]  | epoch 128 | loss 1521.0009 | total time: 1.44s |
[13:06:20-260421]  | epoch 129 | loss 1517.7649 | total time: 1.43s |
[13:06:22-260421]  | epoch 130 | loss 1514.5883 | total time: 1.47s |
[13:06:23-260421]  | epoch 131 | loss 1511.8946 | total time: 1.44s |
[13:06:25-260421]  | epoch 132 | loss 1511.2685 | total time: 1.45s |
[13:06:26-260421]  | epoch 133 | loss 1513.6134 | total time: 1.44s |
[13:06:28-260421]  |

{'ap@5000': (0.08729855449024726, 0.059210641103396966)}
0.08729855449024726


[13:08:07-260421]  | epoch 1 | loss 1891.0369 | total time: 1.46s |
[13:08:08-260421]  | epoch 2 | loss 1815.6472 | total time: 1.44s |
[13:08:09-260421]  | epoch 3 | loss 1807.9684 | total time: 1.45s |
[13:08:11-260421]  | epoch 4 | loss 1809.4407 | total time: 1.45s |
[13:08:12-260421]  | epoch 5 | loss 1798.8437 | total time: 1.47s |
[13:08:14-260421]  | epoch 6 | loss 1800.7002 | total time: 1.45s |
[13:08:15-260421]  | epoch 7 | loss 1789.7741 | total time: 1.43s |
[13:08:17-260421]  | epoch 8 | loss 1772.0428 | total time: 1.45s |
[13:08:18-260421]  | epoch 9 | loss 1759.6452 | total time: 1.45s |
[13:08:20-260421]  | epoch 10 | loss 1732.0851 | total time: 1.44s |
[13:08:21-260421]  | epoch 11 | loss 1731.7663 | total time: 1.44s |
[13:08:23-260421]  | epoch 12 | loss 1721.1899 | total time: 1.46s |
[13:08:24-260421]  | epoch 13 | loss 1715.0625 | total time: 1.46s |
[13:08:25-260421]  | epoch 14 | loss 1707.0846 | total time: 1.44s |
[13:08:27-260421]  | epoch 15 | loss 1693.4

[13:10:59-260421]  | epoch 120 | loss 1569.8418 | total time: 1.45s |
[13:11:00-260421]  | epoch 121 | loss 1563.8610 | total time: 1.43s |
[13:11:02-260421]  | epoch 122 | loss 1559.6108 | total time: 1.46s |
[13:11:03-260421]  | epoch 123 | loss 1566.7830 | total time: 1.45s |
[13:11:05-260421]  | epoch 124 | loss 1553.4166 | total time: 1.44s |
[13:11:06-260421]  | epoch 125 | loss 1556.4232 | total time: 1.45s |
[13:11:08-260421]  | epoch 126 | loss 1555.8669 | total time: 1.46s |
[13:11:09-260421]  | epoch 127 | loss 1563.7170 | total time: 1.46s |
[13:11:11-260421]  | epoch 128 | loss 1559.5770 | total time: 1.43s |
[13:11:12-260421]  | epoch 129 | loss 1563.4136 | total time: 1.46s |
[13:11:14-260421]  | epoch 130 | loss 1563.2912 | total time: 1.45s |
[13:11:15-260421]  | epoch 131 | loss 1558.0612 | total time: 1.44s |
[13:11:16-260421]  | epoch 132 | loss 1550.4075 | total time: 1.45s |
[13:11:18-260421]  | epoch 133 | loss 1565.8690 | total time: 1.44s |
[13:11:19-260421]  |

{'ap@5000': (0.09379456083141363, 0.06243724923895323)}
0.09379456083141363
final printing starts
[[[0.07675139 0.07772712 0.08312229 0.08426506 0.08806899 0.09623729]
  [0.07959878 0.07818614 0.08253671 0.08470585 0.08916005 0.09477349]
  [0.07517342 0.07789751 0.0812105  0.08453752 0.08743356 0.09505027]
  [0.07617809 0.07786981 0.08043084 0.08429253 0.08766263 0.09460886]
  [0.0764019  0.07829176 0.08122078 0.08433398 0.08729018 0.0938346 ]
  [0.07844684 0.07805419 0.08282841 0.08579588 0.08763188 0.0961916 ]
  [0.08154675 0.08400913 0.08653954 0.08799676 0.09104576 0.09735777]
  [0.08809768 0.08862894 0.09030746 0.09374357 0.09477997 0.10291691]]

 [[0.07774562 0.07971265 0.08208173 0.08551934 0.08970099 0.09531154]
  [0.07730935 0.07762285 0.08233288 0.08511635 0.08869761 0.09388847]
  [0.07610746 0.07881033 0.08227031 0.08430348 0.08761354 0.09583553]
  [0.0758636  0.07770319 0.080437   0.08408291 0.08646689 0.09394697]
  [0.0757251  0.07896367 0.08126415 0.08399757 0.08814117 0.

In [9]:
# initial best: dropout=0.5; beta=.1; anneal_steps=10000000
# now best: dropout=0.8; beta=.3; anneal_steps=0
print("starts running")
vae = MultVAE(dec_dims=[200,600,dataset.n_items],
             enc_dims=None,
             dropout=0.8,
             beta=.3,
             anneal_steps=0,
             opt_conf=None,
             device="cpu",
             trainer=None)
print("finishing up")

print("starts running full")
vae_full = MultVAE(dec_dims=[200,600,dataset_full.n_items],
              enc_dims=None,
              dropout=0.8,
              beta=.3,
              anneal_steps=0,
              opt_conf=None,
              device="cpu",
              trainer=None)
print("finishing up full")

starts running
finishing up
starts running full
finishing up full


In [10]:
print("start running")
vae.train(sampler, valid_metric="ndcg@100")
vae_full.train(sampler_full, valid_metric="ndcg@100")

start running


[13:42:17-300421]  | epoch 1 | loss 1948.2683 | total time: 1.61s |
[13:42:18-300421]  | epoch 1 | ndcg@100 0.086 (0.0014) |
[13:42:19-300421]  | epoch 2 | loss 1830.9293 | total time: 1.37s |
[13:42:20-300421]  | epoch 2 | ndcg@100 0.100 (0.0015) |
[13:42:21-300421]  | epoch 3 | loss 1813.5666 | total time: 1.49s |
[13:42:22-300421]  | epoch 3 | ndcg@100 0.106 (0.0015) |
[13:42:24-300421]  | epoch 4 | loss 1811.5289 | total time: 1.58s |
[13:42:25-300421]  | epoch 4 | ndcg@100 0.108 (0.0016) |
[13:42:26-300421]  | epoch 5 | loss 1820.0353 | total time: 1.60s |
[13:42:27-300421]  | epoch 5 | ndcg@100 0.109 (0.0016) |
[13:42:29-300421]  | epoch 6 | loss 1815.2647 | total time: 1.48s |
[13:42:30-300421]  | epoch 6 | ndcg@100 0.111 (0.0016) |
[13:42:31-300421]  | epoch 7 | loss 1794.0294 | total time: 1.51s |
[13:42:32-300421]  | epoch 7 | ndcg@100 0.117 (0.0016) |
[13:42:33-300421]  | epoch 8 | loss 1794.3566 | total time: 1.51s |
[13:42:34-300421]  | epoch 8 | ndcg@100 0.136 (0.0017) |


[13:44:49-300421]  | epoch 66 | loss 1655.3503 | total time: 1.42s |
[13:44:50-300421]  | epoch 66 | ndcg@100 0.268 (0.0023) |
[13:44:51-300421]  | epoch 67 | loss 1653.6700 | total time: 1.44s |
[13:44:52-300421]  | epoch 67 | ndcg@100 0.268 (0.0024) |
[13:44:54-300421]  | epoch 68 | loss 1643.1966 | total time: 1.47s |
[13:44:54-300421]  | epoch 68 | ndcg@100 0.268 (0.0024) |
[13:44:56-300421]  | epoch 69 | loss 1653.1387 | total time: 1.39s |
[13:44:57-300421]  | epoch 69 | ndcg@100 0.269 (0.0024) |
[13:44:58-300421]  | epoch 70 | loss 1649.6767 | total time: 1.45s |
[13:44:59-300421]  | epoch 70 | ndcg@100 0.268 (0.0024) |
[13:45:00-300421]  | epoch 71 | loss 1655.6046 | total time: 1.48s |
[13:45:01-300421]  | epoch 71 | ndcg@100 0.268 (0.0023) |
[13:45:03-300421]  | epoch 72 | loss 1638.6945 | total time: 1.44s |
[13:45:03-300421]  | epoch 72 | ndcg@100 0.269 (0.0024) |
[13:45:05-300421]  | epoch 73 | loss 1653.2529 | total time: 1.42s |
[13:45:05-300421]  | epoch 73 | ndcg@100 0

[13:47:12-300421]  | epoch 130 | ndcg@100 0.263 (0.0023) |
[13:47:14-300421]  | epoch 131 | loss 1598.0931 | total time: 1.47s |
[13:47:14-300421]  | epoch 131 | ndcg@100 0.264 (0.0023) |
[13:47:16-300421]  | epoch 132 | loss 1611.4476 | total time: 1.41s |
[13:47:17-300421]  | epoch 132 | ndcg@100 0.263 (0.0023) |
[13:47:18-300421]  | epoch 133 | loss 1610.3509 | total time: 1.46s |
[13:47:19-300421]  | epoch 133 | ndcg@100 0.263 (0.0023) |
[13:47:20-300421]  | epoch 134 | loss 1599.2266 | total time: 1.42s |
[13:47:21-300421]  | epoch 134 | ndcg@100 0.264 (0.0023) |
[13:47:22-300421]  | epoch 135 | loss 1607.8593 | total time: 1.44s |
[13:47:23-300421]  | epoch 135 | ndcg@100 0.261 (0.0023) |
[13:47:25-300421]  | epoch 136 | loss 1601.4857 | total time: 1.43s |
[13:47:25-300421]  | epoch 136 | ndcg@100 0.262 (0.0023) |
[13:47:27-300421]  | epoch 137 | loss 1606.9400 | total time: 1.43s |
[13:47:28-300421]  | epoch 137 | ndcg@100 0.260 (0.0023) |
[13:47:29-300421]  | epoch 138 | loss 

[13:49:33-300421]  | epoch 194 | ndcg@100 0.252 (0.0022) |
[13:49:34-300421]  | epoch 195 | loss 1575.1750 | total time: 1.46s |
[13:49:35-300421]  | epoch 195 | ndcg@100 0.254 (0.0023) |
[13:49:37-300421]  | epoch 196 | loss 1576.4373 | total time: 1.46s |
[13:49:37-300421]  | epoch 196 | ndcg@100 0.253 (0.0023) |
[13:49:39-300421]  | epoch 197 | loss 1576.1647 | total time: 1.44s |
[13:49:40-300421]  | epoch 197 | ndcg@100 0.253 (0.0023) |
[13:49:41-300421]  | epoch 198 | loss 1575.8869 | total time: 1.43s |
[13:49:42-300421]  | epoch 198 | ndcg@100 0.252 (0.0023) |
[13:49:43-300421]  | epoch 199 | loss 1568.5141 | total time: 1.45s |
[13:49:44-300421]  | epoch 199 | ndcg@100 0.252 (0.0023) |
[13:49:45-300421]  | epoch 200 | loss 1566.9041 | total time: 1.42s |
[13:49:46-300421]  | epoch 200 | ndcg@100 0.252 (0.0023) |


In [12]:
results = evaluate(vae, sampler, ["ap@5000","ndcg@100", "recall@100", "ndcg@20", "recall@20","auc"])
collect_results(results)

results_full = evaluate(vae_full, sampler_full, ["ap@5000","ndcg@100", "recall@100", "ndcg@20", "recall@20","auc"])
collect_results(results_full)

{'ap@5000': (0.09965837007154478, 0.06665599757484941),
 'ndcg@100': (0.25178816109638014, 0.12015208387093138),
 'recall@100': (0.3517595695812736, 0.16947586829359054),
 'ndcg@20': (0.1750354014217612, 0.12419915177981902),
 'recall@20': (0.17557288780578542, 0.117933903467219),
 'auc': (0.8957083, 0.051987235)}

In [13]:
vae.save_model("multivaeHorizontal")
vae = MultVAE(dec_dims=[200,600,dataset.n_items],
              enc_dims=None,
              dropout=0.5,
              beta=.1,
             
              anneal_steps=10000000,
              opt_conf=None,
              device="cpu",
              trainer=None)
vae = vae.load_model("multivaeHorizontal")
results = evaluate(vae, sampler, ["ap@5000"])
collect_results(results)

vae_full.save_model("multivaeHorizontal")
vae_full = MultVAE(dec_dims=[200,600,dataset_full.n_items],
              enc_dims=None,
              dropout=0.5,
              beta=.1,
            
              anneal_steps=10000000,
              opt_conf=None,
              device="cpu",
              trainer=None)
vae_full = vae_full.load_model("multivaeHorizontal")
results = evaluate(vae_full, sampler_full, ["ap@5000"])
collect_results(results_full)

[13:54:59-300421]  Saving MultVAE model checkpoint to multivaeHorizontal...
[13:55:00-300421]  Model checkpoint saved!


{'ap@5000': (0.09965837007154478, 0.06665599757484941)}

In [14]:
sampler.test()
for _, (data_input, ground_truth) in enumerate(sampler):
    data_input, ground_truth = prepare_for_prediction(data_input, ground_truth)
    vae_predictions = vae.predict(*data_input)[0].cpu().numpy()
print(vae_predictions)
print(ground_truth)

print(len(vae_predictions))
print(vae_predictions[0,:])

[[-1.226095    0.79999727  2.52717    ... -2.751881   -1.3040128
  -2.73794   ]
 [ 0.7314098  -0.6896962   1.9279832  ...  1.3332005  -2.445457
   3.0588403 ]
 [ 3.0314856   1.2389275   2.8835135  ...  0.47708693  0.09853566
  -0.79043746]
 ...
 [-0.9842407  -0.9672764   1.1479999  ...  0.3383744  -4.21387
         -inf]
 [-1.5401351   0.6133508   1.7115278  ... -4.338985   -3.7025385
         -inf]
 [-1.0337536  -2.1016026   1.2055782  ... -2.6812234  -0.9415511
  -2.3440714 ]]
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
304
[-1.226095    0.79999727  2.52717    ... -2.751881   -1.3040128
 -2.73794   ]


In [59]:
id2u =  dict(map(reversed, dataset.u2id.items())) #dict for putting user ids back to normal
id2i = dict(map(reversed, dataset.i2id.items())) #dict for translating artist ids back to normal
rectorch_top_n_vae = get_top_artists(vae_predictions, id2u, id2i,100)

done


In [60]:
rectorch_top_n_vae[2251719]

[3083,
 245,
 97,
 429,
 19437,
 4681,
 2258,
 8932,
 55,
 3999,
 283,
 407,
 18365,
 38,
 9991,
 17848,
 17398,
 445,
 56,
 16293,
 1532,
 15520,
 62,
 4487,
 3042,
 17474,
 129,
 135,
 8933,
 368,
 9986,
 15594,
 43,
 6138,
 1825,
 169,
 1483,
 501,
 8731,
 329,
 38942,
 11159,
 220,
 2758,
 31406,
 279,
 1793,
 2907,
 11135,
 16,
 3120,
 17507,
 2562,
 1,
 11084,
 289,
 5891,
 1359,
 60,
 3389,
 8919,
 839,
 6766,
 1894,
 9706,
 3019,
 2828,
 1708,
 93,
 12180,
 17455,
 182,
 2200,
 20118,
 1477,
 15202,
 92,
 17527,
 3008,
 5396,
 5255,
 5818,
 67,
 18152,
 8233,
 1034,
 483,
 15540,
 811,
 12071,
 15867,
 10398,
 8,
 9539,
 9156,
 689,
 1871,
 476,
 3588,
 11237]

In [61]:
# Train and test the four algorithms on our data set
low_gap_r_list = []
medium_gap_r_list = []
high_gap_r_list = []
total_gap_r_list= []
#keeps track of the GAPr of each of the algs

alg_recommendations = [] #Keeps track of how many times each artist was recommended

#Will put for loop here with training, but for now we already have predictions
    
num_times_recommended = pd.DataFrame(artist_dist)
num_times_recommended.columns = ['Recommendation Frequency']
num_times_recommended['Recommendation Frequency'] = 0 #resets for each algorithm
    
    
# resets to 0 before calculating for new alg
low_gap_r = 0
medium_gap_r = 0
high_gap_r = 0
    
#keeps track of group size since it is unpredictable since the test set is selected randomly
num_low_users = 0
num_medium_users = 0
num_high_users = 0
    
#keeps track of the mean absolute error of the current alg
low_mae = 0
medium_mae = 0
high_mae = 0
top_artists = rectorch_top_n_vae #Gets the top N recommendations for each user
    

for user_id, ratings in top_artists.items():
    artist_id_list = [] #user profile size to compute top fraction in GAPr
    for artist_id in ratings:
            
        artist_id_list.append(artist_id)
        num_times_recommended.loc[artist_id] += 1 #increments the number of times the artist was recommended
    if(len(artist_id_list)!=0):
        gap = sum(artist_dist[artist_id_list]/ num_users) / len(artist_id_list) #fraction in numerator for GAPr
    #print("gap:" ,gap)
        if user_id in low_users.index: #summation of all of the top fractions to compute numerator for GAPr
            low_gap_r += gap
            num_low_users += 1 #increments group size to get the denominator to compute GAPr

        elif user_id in medium_users.index:
            medium_gap_r += gap
            num_medium_users += 1

        elif user_id in high_users.index:
            high_gap_r += gap
            num_high_users += 1
alg_recommendations.append(num_times_recommended)
            
total_gap_r = (low_gap_r + medium_gap_r + high_gap_r) / (num_low_users + num_medium_users + num_high_users)
low_gap_r = low_gap_r / num_low_users #Computing GAPr for each group size for each algorithm
medium_gap_r = medium_gap_r / num_medium_users
high_gap_r = high_gap_r / num_high_users

total_gap_r_list.append(total_gap_r)
low_gap_r_list.append(low_gap_r)
medium_gap_r_list.append(medium_gap_r)
high_gap_r_list.append(high_gap_r)

print("done")

done


In [62]:
#Computes change in GAP for each RecSys alg
delta_gap_low_list = []
delta_gap_medium_list = []
delta_gap_high_list = []
delta_gap_total_list = []

for i in range(len(low_gap_r_list)):
    delta_gap_low = ((low_gap_r_list[i] - low_gap_p) / low_gap_p)
    delta_gap_medium = ((medium_gap_r_list[i] - medium_gap_p) / medium_gap_p)
    delta_gap_high = ((high_gap_r_list[i] - high_gap_p) / high_gap_p)
    delta_gap_total = ((total_gap_r_list[i] - total_gap_p) / total_gap_p)
    
    delta_gap_low_list.append(delta_gap_low)
    delta_gap_medium_list.append(delta_gap_medium)
    delta_gap_high_list.append(delta_gap_high)
    delta_gap_total_list.append(delta_gap_total)
    
print(delta_gap_low_list[0])

print(delta_gap_medium_list[0])

print(delta_gap_high_list[0])

print(delta_gap_total_list[0])


1.9033096385277954
1.6938929209190658
1.3369246605336513
1.6241159344719536
